In [1]:
import tensorflow as tf
import numpy as np
from tensorflow.keras import Model, layers, datasets, optimizers


In [15]:
mnist = datasets.mnist

(x_train, y_train), (x_test, y_test) = mnist.load_data()

x_train, x_test = x_train.astype(np.float32)/255, x_test.astype(np.float32)/255
x_train, x_test = np.expand_dims(x_train, axis=3), np.expand_dims(x_test, axis=3)


train = tf.data.Dataset.from_tensor_slices((x_train, y_train)).batch(256)
test = tf.data.Dataset.from_tensor_slices((x_test, y_test)).batch(256)

In [16]:
class basic_model(Model):
    def __init__(self):
        super(basic_model, self).__init__()
        
        self.conv1 = layers.Conv2D(256, (3, 3), padding="same", input_shape=[28, 28, 1])
        self.pool1 = layers.MaxPool2D(pool_size=(2,2))
        self.conv2 = layers.Conv2D(128, (3, 3), padding="same")
        self.pool2 = layers.MaxPool2D(pool_size=(2,2))
        
        self.flatten = layers.Flatten()
        self.fc1 = layers.Dense(80, activation='relu')
        self.fc2 = layers.Dense(10)
        
    def call(self, inputs):
        x = self.conv1(inputs)
        x = self.pool1(x)
        x = self.conv2(x)
        x = self.pool2(x)
        x = self.flatten(x)
        x = self.fc1(x)
        x = self.fc2(x)
        return x 
    
class basic_model_2(Model):
    def __init__(self):
        super(basic_model, self).__init__()
        
        model = models.Sequential()
        model.add(layers.Dense(20))
        model.add(activation='relu')
        model.add(layers.Dense(10))

        
    def call(self, inputs):
        x = tf.convert_to_tensor(inputs)

        return self.model(x)

In [17]:
image_size = 28*28
num_epochs = 100
batch_size = 256
learning_rate = 1e-3

model = basic_model()
model.build(input_shape=(None, 28, 28, 1))
model.summary()
optimizer = optimizers.Adam(learning_rate=learning_rate)

Model: "basic_model_3"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
conv2d_6 (Conv2D)            multiple                  2560      
_________________________________________________________________
max_pooling2d_6 (MaxPooling2 multiple                  0         
_________________________________________________________________
conv2d_7 (Conv2D)            multiple                  295040    
_________________________________________________________________
max_pooling2d_7 (MaxPooling2 multiple                  0         
_________________________________________________________________
flatten_3 (Flatten)          multiple                  0         
_________________________________________________________________
dense_6 (Dense)              multiple                  501840    
_________________________________________________________________
dense_7 (Dense)              multiple                

In [26]:
for epoch in range(num_epochs):
    for step, (x, y) in enumerate(train):
        with tf.GradientTape() as tape:
            logits = model(x)
            
            loss = tf.nn.sigmoid_cross_entropy_with_logits(labels=tf.one_hot(y, depth=10), logits=logits)
            
        gradients = tape.gradient(loss, model.trainable_variables)
        optimizer.apply_gradients(zip(gradients, model.trainable_variables))
        
        if step % 10 == 0:
            print(epoch, step, 'loss:', loss.numpy())
            
            
    model.save_weights('./my_model')

0 0 loss: [[3.13369201e-05 9.15374549e-05 1.82259567e-02 ... 3.64208757e-03
  3.06172878e-04 2.10835096e-05]
 [1.34916932e-04 1.51771800e-07 2.56671850e-03 ... 2.63250637e-04
  5.31944854e-04 4.69596671e-05]
 [1.32590387e-04 2.02970416e-03 3.28293099e-04 ... 4.16822237e-04
  1.47183817e-02 1.43906977e-02]
 ...
 [3.65889500e-05 4.17226431e-08 5.18199406e-04 ... 5.24613153e-09
  2.97228951e-04 3.55560026e-08]
 [9.48386453e-03 3.73202842e-03 3.15111451e-04 ... 7.03135538e-06
  4.06066477e-02 4.14541049e-04]
 [1.22168785e-05 4.44644457e-03 2.74007823e-02 ... 7.32306802e-08
  1.40369749e-02 6.60919625e-07]]
0 10 loss: [[2.34059644e-05 1.02985296e-05 3.52019447e-06 ... 7.80065893e-05
  1.13684116e-02 1.07203402e-01]
 [1.73302193e-04 9.92806008e-07 3.34716424e-05 ... 2.07229357e-04
  2.41120420e-02 1.06798514e-04]
 [6.09024719e-05 6.65502856e-04 1.52734356e-05 ... 1.63168870e-02
  6.33267174e-03 1.62345022e-01]
 ...
 [1.77303761e-01 8.27569480e-08 1.88711874e-05 ... 4.74969738e-06
  4.2621174

0 140 loss: [[7.0721311e-05 7.5138887e-05 1.6477117e-05 ... 1.5861944e-03
  4.4538105e-05 3.1752023e-03]
 [5.7365603e-05 1.4885576e-05 1.2258436e-03 ... 2.0063933e-07
  8.8779271e-02 6.7336122e-03]
 [5.0592067e-04 3.1780105e-02 3.3230212e-02 ... 1.4692035e-01
  1.1722461e-04 2.4103440e-02]
 ...
 [1.1645935e-08 7.5887993e-04 1.8205560e-06 ... 7.1092662e-03
  2.3506639e-04 1.9210802e-05]
 [6.8435846e-05 3.5212570e-04 1.2519928e-04 ... 1.3956826e-05
  5.2080047e-04 4.0285944e-05]
 [2.1161104e-03 5.3471206e-03 3.1375446e-04 ... 1.7060556e-02
  1.4494971e-04 2.5722773e-05]]
0 150 loss: [[3.13189230e-04 2.05578508e-05 5.73609541e-05 ... 2.21249437e-08
  7.36746779e-06 1.82126939e-10]
 [6.28886028e-06 9.67157732e-08 8.92576203e-03 ... 7.77410278e-08
  9.01685715e-01 1.59589337e-08]
 [1.68554434e-05 3.14339559e-05 1.32512268e-05 ... 6.26198074e-04
  1.02260022e-03 2.07054033e-03]
 ...
 [6.54260875e-05 4.71579995e-07 1.32101355e-02 ... 3.80675832e-04
  3.47794878e-04 1.23071266e-04]
 [9.9575532

1 40 loss: [[1.6034752e-03 1.2372755e-07 5.5663800e-04 ... 1.7277795e-04
  1.0827490e-04 1.0937901e-05]
 [1.3427312e-03 4.1792812e-04 3.9236684e-06 ... 3.7982341e-04
  7.1087733e-02 5.5493605e-03]
 [6.0357247e-04 7.1770863e-08 2.0894076e-05 ... 3.0086257e-03
  1.3129844e-04 1.2566565e-04]
 ...
 [8.6837371e-10 1.6138742e-06 4.1279759e-06 ... 1.3407161e-04
  7.3680158e-06 2.7983609e-07]
 [2.1431930e-07 1.0355385e-05 2.8603077e-07 ... 4.1557394e-04
  5.3756135e-03 8.5910661e-03]
 [1.9162127e-07 2.1303957e-07 1.4336799e-08 ... 2.7799683e-03
  9.7003125e-05 2.4118591e-03]]
1 50 loss: [[1.23980630e-03 6.84941964e-11 2.89698594e-08 ... 1.81934040e-04
  1.15618086e-03 2.25184504e-05]
 [8.08376444e-06 1.11073814e-05 3.37402416e-05 ... 4.95643260e-09
  2.08466896e-04 1.69366639e-11]
 [2.28774320e-06 1.26782396e-09 4.13240748e-04 ... 5.53395075e-04
  1.37002161e-03 1.56363328e-07]
 ...
 [2.61901319e-03 4.20627557e-03 5.73620375e-04 ... 4.09312472e-02
  7.32915578e-06 1.77478716e-01]
 [5.15115653e

1 180 loss: [[2.0473342e-07 3.3351846e-09 1.0435233e-06 ... 6.1319923e-05
  2.2158960e-05 9.4192357e-05]
 [1.8798141e-06 5.0419853e-06 5.3865890e-05 ... 2.2391545e-02
  2.2476927e-07 3.9983275e-05]
 [6.9152550e-10 2.0352306e-06 3.8688218e-03 ... 3.9575662e-02
  1.4845763e-07 7.3368568e-11]
 ...
 [2.9515080e-05 9.7636021e-06 3.8276994e-08 ... 1.3331039e-04
  7.1260321e-05 3.7422091e-05]
 [7.2011921e-05 8.0961880e-04 4.7760882e-06 ... 8.1744732e-04
  1.9102509e-04 2.3937611e-07]
 [2.5187837e-06 1.3156022e-03 3.5221427e-07 ... 7.9692289e-04
  8.4053242e-04 3.3757670e-09]]
1 190 loss: [[1.1709755e-06 2.8623480e-04 2.9849380e-05 ... 2.5154638e-06
  7.4576838e-07 2.2204684e-11]
 [1.9942638e-06 1.0886166e-06 1.4083955e-04 ... 1.7875101e-08
  1.0409715e-05 6.3388600e-11]
 [1.9941275e-07 1.4435174e-04 7.1677245e-04 ... 6.0511542e-07
  4.1831691e-02 1.9053248e-07]
 ...
 [8.1795542e-07 2.6963438e-05 9.4629551e-04 ... 2.3606415e-03
  4.0250136e-08 6.0066403e-05]
 [5.7134706e-01 1.0180738e-04 1.632

2 80 loss: [[4.52655058e-07 2.08008090e-11 1.91418536e-07 ... 1.50400536e-09
  1.74969989e-06 1.36452571e-10]
 [1.57720083e-03 5.36736388e-06 2.96030543e-04 ... 5.49011538e-08
  4.53311685e-07 1.95974707e-07]
 [1.33383751e-03 2.81955045e-06 6.43998384e-03 ... 1.07263654e-01
  8.52626181e-05 2.96523067e-05]
 ...
 [7.85456621e-07 1.32227224e-05 1.57748782e-05 ... 1.76983997e-10
  1.41922967e-04 6.59928926e-13]
 [1.23816903e-07 3.61809271e-09 3.80770402e-08 ... 1.50809018e-02
  9.04124172e-05 9.38950200e-03]
 [1.97432351e+00 1.96519323e-07 2.38593111e-06 ... 7.39880046e-03
  3.71261763e-07 5.01922941e+00]]
2 90 loss: [[3.2416928e-08 2.3012840e-08 8.7767658e-05 ... 2.2828253e-07
  1.4015246e-05 3.5397504e-13]
 [1.0214794e-03 2.0632641e-02 4.4926084e-05 ... 9.6476913e-07
  1.2307027e-05 2.0326877e-06]
 [3.5147230e-05 7.0226895e-07 4.9195037e-06 ... 2.3859362e-05
  9.2434289e-04 2.6873944e-04]
 ...
 [3.8301005e-05 3.9842897e-04 5.8705855e-06 ... 1.6040141e-06
  1.5243232e-08 2.7142855e-06]
 

...

417 50 loss: [[0.000000e+00 0.000000e+00 0.000000e+00 ... 0.000000e+00 0.000000e+00
  0.000000e+00]
 [0.000000e+00 0.000000e+00 0.000000e+00 ... 0.000000e+00 0.000000e+00
  0.000000e+00]
 [0.000000e+00 0.000000e+00 0.000000e+00 ... 0.000000e+00 0.000000e+00
  0.000000e+00]
 ...
 [0.000000e+00 9.727837e-27 0.000000e+00 ... 6.688831e-17 0.000000e+00
  5.988599e-12]
 [0.000000e+00 0.000000e+00 0.000000e+00 ... 0.000000e+00 0.000000e+00
  2.041973e-38]
 [0.000000e+00 0.000000e+00 0.000000e+00 ... 0.000000e+00 0.000000e+00
  0.000000e+00]]
417 60 loss: [[2.5675103e-36 0.0000000e+00 3.8418709e-36 ... 1.4370956e-32
  6.4900965e-30 1.1303299e-29]
 [4.8421459e-38 2.0503014e-23 0.0000000e+00 ... 2.5484598e-31
  3.0643054e-35 0.0000000e+00]
 [0.0000000e+00 0.0000000e+00 0.0000000e+00 ... 1.5941808e-34
  0.0000000e+00 0.0000000e+00]
 ...
 [0.0000000e+00 0.0000000e+00 1.9616174e-33 ... 0.0000000e+00
  0.0000000e+00 0.0000000e+00]
 [0.0000000e+00 3.8464298e-37 5.0990294e-32 ... 5.8609373e-32
  0.000

417 200 loss: [[4.1171998e-36 1.1566297e-25 0.0000000e+00 ... 0.0000000e+00
  2.0000277e-30 7.6786534e-23]
 [0.0000000e+00 0.0000000e+00 0.0000000e+00 ... 0.0000000e+00
  0.0000000e+00 0.0000000e+00]
 [0.0000000e+00 0.0000000e+00 0.0000000e+00 ... 0.0000000e+00
  0.0000000e+00 0.0000000e+00]
 ...
 [0.0000000e+00 7.1432050e-19 0.0000000e+00 ... 0.0000000e+00
  0.0000000e+00 0.0000000e+00]
 [0.0000000e+00 0.0000000e+00 0.0000000e+00 ... 0.0000000e+00
  1.3501939e-28 0.0000000e+00]
 [0.0000000e+00 0.0000000e+00 0.0000000e+00 ... 0.0000000e+00
  0.0000000e+00 0.0000000e+00]]
417 210 loss: [[0.0000000e+00 0.0000000e+00 0.0000000e+00 ... 0.0000000e+00
  5.8050311e-36 4.8202430e-19]
 [0.0000000e+00 0.0000000e+00 0.0000000e+00 ... 0.0000000e+00
  0.0000000e+00 0.0000000e+00]
 [0.0000000e+00 2.3714268e-36 2.4155444e-13 ... 0.0000000e+00
  1.7822752e-33 0.0000000e+00]
 ...
 [0.0000000e+00 0.0000000e+00 0.0000000e+00 ... 0.0000000e+00
  0.0000000e+00 0.0000000e+00]
 [0.0000000e+00 3.7241359e-37 0

418 110 loss: [[0.0000000e+00 0.0000000e+00 2.7734641e-35 ... 0.0000000e+00
  0.0000000e+00 1.1083143e-38]
 [0.0000000e+00 0.0000000e+00 0.0000000e+00 ... 0.0000000e+00
  0.0000000e+00 0.0000000e+00]
 [8.6839579e-20 0.0000000e+00 0.0000000e+00 ... 0.0000000e+00
  2.1056235e-34 0.0000000e+00]
 ...
 [0.0000000e+00 0.0000000e+00 0.0000000e+00 ... 2.3908201e-28
  9.8625763e-27 8.3267082e-16]
 [1.0689951e-30 0.0000000e+00 0.0000000e+00 ... 0.0000000e+00
  2.0946110e-31 6.8840478e-30]
 [0.0000000e+00 0.0000000e+00 0.0000000e+00 ... 0.0000000e+00
  0.0000000e+00 0.0000000e+00]]
418 120 loss: [[0.0000000e+00 0.0000000e+00 9.7932065e-22 ... 0.0000000e+00
  5.9893725e-28 0.0000000e+00]
 [1.1449337e-35 0.0000000e+00 0.0000000e+00 ... 0.0000000e+00
  1.6777873e-36 0.0000000e+00]
 [0.0000000e+00 0.0000000e+00 6.0490674e-37 ... 1.4221562e-35
  0.0000000e+00 0.0000000e+00]
 ...
 [0.0000000e+00 0.0000000e+00 0.0000000e+00 ... 0.0000000e+00
  0.0000000e+00 0.0000000e+00]
 [0.0000000e+00 0.0000000e+00 0

419 20 loss: [[0.0000000e+00 0.0000000e+00 0.0000000e+00 ... 0.0000000e+00
  0.0000000e+00 0.0000000e+00]
 [0.0000000e+00 0.0000000e+00 0.0000000e+00 ... 0.0000000e+00
  0.0000000e+00 0.0000000e+00]
 [0.0000000e+00 0.0000000e+00 0.0000000e+00 ... 0.0000000e+00
  0.0000000e+00 5.1077835e-27]
 ...
 [0.0000000e+00 0.0000000e+00 0.0000000e+00 ... 0.0000000e+00
  0.0000000e+00 0.0000000e+00]
 [0.0000000e+00 0.0000000e+00 0.0000000e+00 ... 0.0000000e+00
  0.0000000e+00 0.0000000e+00]
 [0.0000000e+00 2.3893437e-35 6.5763981e-31 ... 0.0000000e+00
  0.0000000e+00 0.0000000e+00]]
419 30 loss: [[0.0000000e+00 0.0000000e+00 0.0000000e+00 ... 2.4465653e-35
  4.3300573e-36 1.1070187e-35]
 [0.0000000e+00 0.0000000e+00 0.0000000e+00 ... 0.0000000e+00
  1.1048011e-25 0.0000000e+00]
 [2.1099444e-31 0.0000000e+00 3.6246515e-37 ... 0.0000000e+00
  1.4384763e-34 0.0000000e+00]
 ...
 [0.0000000e+00 4.6289865e-36 0.0000000e+00 ... 1.7595389e-38
  0.0000000e+00 0.0000000e+00]
 [0.0000000e+00 0.0000000e+00 0.0

KeyboardInterrupt: 